# Trying For Question Answering model 
* Subject- Theory of Computation

In [1]:
import faiss
import numpy as np
from transformers import AutoTokenizer, AutoModelForSeq2SeqLM, pipeline
from langchain_community.document_loaders import WikipediaLoader
from bs4 import BeautifulSoup
import requests
from sentence_transformers import SentenceTransformer
from langchain_text_splitters import CharacterTextSplitter
from langchain.chains import RetrievalQA
from langchain.llms import HuggingFacePipeline
from langchain.prompts import PromptTemplate
from langchain.schema import StrOutputParser
from langchain.schema.runnable import RunnablePassthrough
import requests
from bs4 import BeautifulSoup
import pandas as pd
import fitz  # PyMuPDF

c:\Users\ACER 5\Desktop\ASHWINI KAKDE\Langchain\langchain\lib\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


# Load Documents from Multiple Sources:

In [2]:
# Define a function to load data from URLs
def load_data_from_url(url):
    response = requests.get(url)
    soup = BeautifulSoup(response.content, features="lxml")
    return soup.get_text()

# Define a function to load data from PDFs
def load_data_from_pdf(pdf_path):
    document = fitz.open(pdf_path)
    pdf_text = ""
    for page_num in range(len(document)):
        page = document[page_num]
        pdf_text += page.get_text()
    return pdf_text

# Load content from URLs
javatpoint_url = "https://www.javatpoint.com/automata-tutorial"
geeksforgeeks_url = "https://www.geeksforgeeks.org/introduction-of-theory-of-computation/"
geektonight_url = "https://www.geektonight.com/theory-of-computation-notes/"

javatpoint_content = load_data_from_url(javatpoint_url)
geeksforgeeks_content = load_data_from_url(geeksforgeeks_url)
geektonight_content = load_data_from_url(geektonight_url)

# Load content from PDFs
pdf_path1 = "theory-of-computation.pdf"
pdf_path2 = "toc-klp-mishra.pdf"

pdf_content1 = load_data_from_pdf(pdf_path1)
pdf_content2 = load_data_from_pdf(pdf_path2)

# Combine content from URLs
url_content = "\n\n".join([javatpoint_content, geeksforgeeks_content, geektonight_content])

# Combine content from PDFs
pdf_content = "\n\n".join([pdf_content1, pdf_content2])

# Combine content from both sources
combined_content = "\n\n".join([url_content, pdf_content])

# Save combined content to a text file with UTF-8 encoding
with open("combined_theory_of_computation_content.txt", "w", encoding="utf-8") as file:
    file.write(combined_content)

In [3]:
combined_content

'Automata Tutorial | Theory of Computation - JavatpointTutorials×PythonPython Django Numpy Pandas Tkinter Pytorch Flask OpenCVAI, ML and Data ScienceArtificial Intelligence Machine Learning Data Science Deep Learning TensorFlow Artificial Neural Network Matplotlib Python ScipyJavaJava Servlet JSP Spring Boot Spring Framework Hibernate JavaFX Java Web ServicesB.Tech and MCADBMS Data Structures Operating System Computer Network DAA Computer Organization Software Engineering Data MiningWeb TechnologyHTML CSS JavaScript Jquery Angular-8 React JS React Native Node JSSoftware TestingSoftware Testing Selenium JIRA JMeter Postman TestNG SoapUI CucumberInterview×Technical InterviewC C++ Php Java Python JavaScript TypeScriptJava InterviewJDBC Servlet Maven Jenkins Spring Spring Boot JDB Hibernate JSFWeb InterviewHTML CSS JavaScript Jquery Angular Node-JS AJAXDatabase InterviewDBMS SQL PL/SQL Oracle MySQL MongoDB Redis MariaDBCompany InterviewsIBM Adobe Microsoft Amazon TCS HCL Wipro DXC Accentur

In [18]:
# Function to clean text
import re 
def clean_text(text):
  # Remove URLs, HTML tags, etc.
  text = re.sub(r"http\S+", "", text)  # Remove URLs
  text = re.sub(r"<[^>]*>", "", text)  # Remove HTML tags
  # You can add more cleaning steps here
  return text

# Load Combined Data 

In [19]:
from langchain_community.document_loaders import TextLoader

# Ensure the TextLoader uses UTF-8 encoding
loader = TextLoader("combined_theory_of_computation_content.txt", encoding="utf-8")
loaded_data = loader.load()
print("Loaded data successfully")

Loaded data successfully


In [20]:
loaded_data

[Document(metadata={'source': 'combined_theory_of_computation_content.txt'}, page_content='Automata Tutorial | Theory of Computation - JavatpointTutorials×PythonPython Django Numpy Pandas Tkinter Pytorch Flask OpenCVAI, ML and Data ScienceArtificial Intelligence Machine Learning Data Science Deep Learning TensorFlow Artificial Neural Network Matplotlib Python ScipyJavaJava Servlet JSP Spring Boot Spring Framework Hibernate JavaFX Java Web ServicesB.Tech and MCADBMS Data Structures Operating System Computer Network DAA Computer Organization Software Engineering Data MiningWeb TechnologyHTML CSS JavaScript Jquery Angular-8 React JS React Native Node JSSoftware TestingSoftware Testing Selenium JIRA JMeter Postman TestNG SoapUI CucumberInterview×Technical InterviewC C++ Php Java Python JavaScript TypeScriptJava InterviewJDBC Servlet Maven Jenkins Spring Spring Boot JDB Hibernate JSFWeb InterviewHTML CSS JavaScript Jquery Angular Node-JS AJAXDatabase InterviewDBMS SQL PL/SQL Oracle MySQL Mo

In [21]:
loaded_data[0].metadata

{'source': 'combined_theory_of_computation_content.txt'}

In [22]:
loaded_data[0].metadata['source']

'combined_theory_of_computation_content.txt'

In [23]:
loaded_data[0].page_content

'Automata Tutorial | Theory of Computation - JavatpointTutorials×PythonPython Django Numpy Pandas Tkinter Pytorch Flask OpenCVAI, ML and Data ScienceArtificial Intelligence Machine Learning Data Science Deep Learning TensorFlow Artificial Neural Network Matplotlib Python ScipyJavaJava Servlet JSP Spring Boot Spring Framework Hibernate JavaFX Java Web ServicesB.Tech and MCADBMS Data Structures Operating System Computer Network DAA Computer Organization Software Engineering Data MiningWeb TechnologyHTML CSS JavaScript Jquery Angular-8 React JS React Native Node JSSoftware TestingSoftware Testing Selenium JIRA JMeter Postman TestNG SoapUI CucumberInterview×Technical InterviewC C++ Php Java Python JavaScript TypeScriptJava InterviewJDBC Servlet Maven Jenkins Spring Spring Boot JDB Hibernate JSFWeb InterviewHTML CSS JavaScript Jquery Angular Node-JS AJAXDatabase InterviewDBMS SQL PL/SQL Oracle MySQL MongoDB Redis MariaDBCompany InterviewsIBM Adobe Microsoft Amazon TCS HCL Wipro DXC Accentur

# Cleaning of Data removing urls from document

In [24]:
# Clean the documents
cleaned_documents = [Document(page_content=clean_text(doc.page_content)) for doc in loaded_data]
cleaned_documents

[Document(metadata={}, page_content='Automata Tutorial | Theory of Computation - JavatpointTutorials×PythonPython Django Numpy Pandas Tkinter Pytorch Flask OpenCVAI, ML and Data ScienceArtificial Intelligence Machine Learning Data Science Deep Learning TensorFlow Artificial Neural Network Matplotlib Python ScipyJavaJava Servlet JSP Spring Boot Spring Framework Hibernate JavaFX Java Web ServicesB.Tech and MCADBMS Data Structures Operating System Computer Network DAA Computer Organization Software Engineering Data MiningWeb TechnologyHTML CSS JavaScript Jquery Angular-8 React JS React Native Node JSSoftware TestingSoftware Testing Selenium JIRA JMeter Postman TestNG SoapUI CucumberInterview×Technical InterviewC C++ Php Java Python JavaScript TypeScriptJava InterviewJDBC Servlet Maven Jenkins Spring Spring Boot JDB Hibernate JSFWeb InterviewHTML CSS JavaScript Jquery Angular Node-JS AJAXDatabase InterviewDBMS SQL PL/SQL Oracle MySQL MongoDB Redis MariaDBCompany InterviewsIBM Adobe Microso

# Split Loaded Data into Smaller Chunks 

In [44]:
from langchain_text_splitters import RecursiveCharacterTextSplitter
import pandas as pd

# Initialize the recursive text splitter with adjusted separators
text_splitter = RecursiveCharacterTextSplitter(
    separators=["\n\n", "\n", " ", ""],
    chunk_size=512,
    chunk_overlap=100,
    length_function=len,
)

# Load combined content from file
with open("combined_theory_of_computation_content.txt", "r", encoding="utf-8") as file:
    cleaned_documents = file.read()

In [45]:
# Split the content into documents
from langchain.docstore.document import Document
# Create a Document object from the content
document=Document(page_content=cleaned_documents)
# Split the content into documents
documents = text_splitter.split_documents([document])
documents

[Document(metadata={}, page_content='Automata Tutorial | Theory of Computation - JavatpointTutorials×PythonPython Django Numpy Pandas Tkinter Pytorch Flask OpenCVAI, ML and Data ScienceArtificial Intelligence Machine Learning Data Science Deep Learning TensorFlow Artificial Neural Network Matplotlib Python ScipyJavaJava Servlet JSP Spring Boot Spring Framework Hibernate JavaFX Java Web ServicesB.Tech and MCADBMS Data Structures Operating System Computer Network DAA Computer Organization Software Engineering Data MiningWeb TechnologyHTML CSS'),
 Document(metadata={}, page_content='Computer Network DAA Computer Organization Software Engineering Data MiningWeb TechnologyHTML CSS JavaScript Jquery Angular-8 React JS React Native Node JSSoftware TestingSoftware Testing Selenium JIRA JMeter Postman TestNG SoapUI CucumberInterview×Technical InterviewC C++ Php Java Python JavaScript TypeScriptJava InterviewJDBC Servlet Maven Jenkins Spring Spring Boot JDB Hibernate JSFWeb InterviewHTML CSS Jav

In [46]:
len(documents)

2151

In [47]:
documents[0].page_content

'Automata Tutorial | Theory of Computation - JavatpointTutorials×PythonPython Django Numpy Pandas Tkinter Pytorch Flask OpenCVAI, ML and Data ScienceArtificial Intelligence Machine Learning Data Science Deep Learning TensorFlow Artificial Neural Network Matplotlib Python ScipyJavaJava Servlet JSP Spring Boot Spring Framework Hibernate JavaFX Java Web ServicesB.Tech and MCADBMS Data Structures Operating System Computer Network DAA Computer Organization Software Engineering Data MiningWeb TechnologyHTML CSS'

In [48]:
len(documents)

2151

# Generate Embedding 
* initialize the tokenizer and model for hugging face embeddings

In [49]:
# Initialize tokenizer and model for Hugging Face embeddings
from transformers import AutoTokenizer, AutoModel,AutoModelForQuestionAnswering, pipeline
from langchain.vectorstores import Chroma
from langchain.embeddings import HuggingFaceEmbeddings
# Initialize the HuggingFaceEmbeddings class with a model name
# Initialize the HuggingFaceEmbeddings class with a model name
embedding_model = HuggingFaceEmbeddings(model_name="sentence-transformers/all-mpnet-base-v2")

# Initialize Chroma collection and add documents with embeddings

In [50]:
# Initialize Chroma collection with embedding function
vectordb = Chroma(
    persist_directory='toc_db',
    embedding_function=embedding_model  # Pass the entire embedding_model object
)


In [51]:
vectordb

# Load tokenizer and model for question-answering

In [55]:
# Initialize a language model for question answering
model_name = "google/flan-t5-xl"  # Using a large model for better performance
tokenizer = AutoTokenizer.from_pretrained(model_name)
model = AutoModelForSeq2SeqLM.from_pretrained(model_name)

Loading checkpoint shards: 100%|██████████| 2/2 [00:00<00:00,  2.46it/s]


In [56]:
model

T5ForConditionalGeneration(
  (shared): Embedding(32128, 2048)
  (encoder): T5Stack(
    (embed_tokens): Embedding(32128, 2048)
    (block): ModuleList(
      (0): T5Block(
        (layer): ModuleList(
          (0): T5LayerSelfAttention(
            (SelfAttention): T5Attention(
              (q): Linear(in_features=2048, out_features=2048, bias=False)
              (k): Linear(in_features=2048, out_features=2048, bias=False)
              (v): Linear(in_features=2048, out_features=2048, bias=False)
              (o): Linear(in_features=2048, out_features=2048, bias=False)
              (relative_attention_bias): Embedding(32, 32)
            )
            (layer_norm): T5LayerNorm()
            (dropout): Dropout(p=0.1, inplace=False)
          )
          (1): T5LayerFF(
            (DenseReluDense): T5DenseGatedActDense(
              (wi_0): Linear(in_features=2048, out_features=5120, bias=False)
              (wi_1): Linear(in_features=2048, out_features=5120, bias=False)
       

* The pipeline() function from the transformers library is used to create a pipeline for text generation. It takes several arguments to configure the pipeline's behavior:

* Arguments:

1. text2text-generation: This specifies the task that the pipeline will perform. In this case, it will be used for text generation.
2. model: This is the pre-trained language model that will be used for text generation. It should be an instance of AutoModelForSeq2SeqLM.
3. tokenizer: This is the tokenizer associated with the language model. It is used to convert text into a sequence of numerical tokens that the model can understand.
4. max_length: This sets the maximum length of the generated text sequence. If the generated sequence exceeds this length, it will be truncated.
5. num_return_sequences: This specifies the number of generated text sequences that will be returned. In this case, only one sequence will be returned.
6. do_sample: This determines whether to use sampling or greedy decoding to generate the text. If True, sampling will be used, which introduces randomness and can generate more diverse outputs. If False, greedy decoding will be used, which tends to generate more deterministic and repetitive outputs.
7. temperature: This controls the randomness of the sampling process. A higher temperature leads to more diverse and creative outputs, while a lower temperature leads to more focused and predictable outputs.

In [84]:
# Create a text2text-generation pipeline with a larger max_length
text_generation_pipeline = pipeline(
    "text2text-generation",
    model=model,
    tokenizer=tokenizer,
    max_length=1024,
    num_return_sequences=3,
    do_sample=True,
    temperature=0.3,
)

# Create pipeline for question answering model

In [85]:
# Wrap the pipeline in a LangChain HuggingFacePipeline
llm = HuggingFacePipeline(pipeline=text_generation_pipeline)

In [86]:
# Create a custom prompt template for detailed answers
detailed_prompt_template = """You are an expert professor in Theory of Computation. A student has asked you the following question:

{question}

Using the following information as a starting point, provide a comprehensive and detailed answer. Make sure to explain all relevant concepts thoroughly:

{context}

Your detailed answer:
"""
DETAILED_PROMPT = PromptTemplate(
    template=detailed_prompt_template, input_variables=["context", "question"]
)


In [87]:
# Create a retriever
retriever = vectordb.as_retriever(search_kwargs={"k": 5})
retriever

VectorStoreRetriever(tags=['Chroma', 'HuggingFaceEmbeddings'], vectorstore=<langchain_community.vectorstores.chroma.Chroma object at 0x000001AF1FC84FD0>, search_kwargs={'k': 5})

In [88]:
# Define the chain
def format_docs(docs):
    return "\n\n".join(doc.page_content for doc in docs)

In [89]:
chain = (
    {"context": retriever | format_docs, "question": RunnablePassthrough()}
    | DETAILED_PROMPT
    | llm
    | StrOutputParser()
)

In [90]:
chain

{
  context: VectorStoreRetriever(tags=['Chroma', 'HuggingFaceEmbeddings'], vectorstore=<langchain_community.vectorstores.chroma.Chroma object at 0x000001AF1FC84FD0>, search_kwargs={'k': 5})
           | RunnableLambda(format_docs),
  question: RunnablePassthrough()
}
| PromptTemplate(input_variables=['context', 'question'], input_types={}, partial_variables={}, template='You are an expert professor in Theory of Computation. A student has asked you the following question:\n\n{question}\n\nUsing the following information as a starting point, provide a comprehensive and detailed answer. Make sure to explain all relevant concepts thoroughly:\n\n{context}\n\nYour detailed answer:\n')
| HuggingFacePipeline(pipeline=<transformers.pipelines.text2text_generation.Text2TextGenerationPipeline object at 0x000001AF2D4EB250>)
| StrOutputParser()

In [91]:
# Function to ask TOC-related questions
def ask_toc_question(question):
    return chain.invoke(question)

# Getting answer 

In [92]:
# Example usage
toc_questions = [
    "What is a Regular Expression in Theory of Computation?",
    "Explain the concept of a Turing Machine.",
    "What is the difference between DFA and NFA?",
    "Describe the Chomsky Hierarchy in TOC.",
    "What is the Pumping Lemma used for in TOC?"
]

In [93]:
single_question = "What is the Pumping Lemma used for in TOC?"
answer = ask_toc_question(single_question)
print(f"Question: {single_question}")
print(f"Answer: {answer}")

Question: What is the Pumping Lemma used for in TOC?
Answer: The Pumping Lemma is used in Theory of Computation to prove the NP-completeness of a search problem.
